In [1]:
! git clone https://github.com/uf-hobi-informatics-lab/ClinicalTransformerNER.git

fatal: destination path 'ClinicalTransformerNER' already exists and is not an empty directory.


In [4]:
import sys
sys.path.append("./ClinicalTransformerNER/")
sys.path.append("./NLPpreprocessing-master/")

In [5]:
import os
from pathlib import Path
from collections import defaultdict, Counter
import numpy as np
from sklearn.model_selection import train_test_split
import shutil 

In [6]:
from annotation2BIO import generate_BIO, pre_processing, read_annotation_brat, BIOdata_to_file
MIMICIII_PATTERN = "\[\*\*|\*\*\]"

In [7]:
! ls

2018n2c2			       DR_note_selection.ipynb
brat_eval.py			       log2.txt
ClinicalTransformerNER		       log_bert.txt
ClinicalTransformerRelationExtraction  new_saved_models
data				       NLPpreprocessing-master
DR_ner.ipynb			       result
DR_ner_second_round.ipynb	       saved_models
DR_notes


In [2]:
! pwd

/home/zehao.yu/workspace/py3/dr_ann


In [2]:
training_root = "./data/all_annotated_notes_new/"

# Pre_process

In [8]:
i=0
file_ids=set()
for fn in Path(training_root).glob("*.ann"):
    file_ids.add(fn.stem)
    _, ens, _ = read_annotation_brat(fn)
    if len(ens)==0:
        print(fn)
#         fn_txt=str(fn).split('.')[0]+'.txt'
#         os.remove(fn)
#         os.remove(fn_txt)
#print(i)
    

data/all_annotated_notes_new/note_161.ann
data/all_annotated_notes_new/note_836.ann
data/all_annotated_notes_new/note_980.ann
data/all_annotated_notes_new/note_93.ann
data/all_annotated_notes_new/note_830.ann
data/all_annotated_notes_new/note_7753.ann
data/all_annotated_notes_new/note_658.ann
data/all_annotated_notes_new/note_1081.ann
data/all_annotated_notes_new/note_1533.ann
data/all_annotated_notes_new/note_933.ann
data/all_annotated_notes_new/note_1664.ann
data/all_annotated_notes_new/note_737.ann
data/all_annotated_notes_new/note_1574.ann


In [9]:
len(file_ids)


391

In [10]:
# Brief descriptive statistics
file_ids = set()
enss = []

for fn in Path(training_root).glob("*.ann"):
    file_ids.add(fn.stem)
    _, ens, _ = read_annotation_brat(fn)
    #print( _)
    enss.extend(ens)
print("training files: ", len(file_ids), list(file_ids)[:5])
print("total training eneitites: ", len(enss))
print("Entities distribution by types:\n", "\n".join([str(c) for c in Counter([each[1] for each in enss]).most_common()]))

training files:  391 ['note_7515', 'note_7940', 'note_3194', 'note_3006', 'note_8106']
total training eneitites:  4458
Entities distribution by types:
 ('lesion', 2473)
('laterality', 1330)
('severity', 606)
('eye_part', 49)


In [11]:
#split train and test annotation
file_ids = list(file_ids)
train_dev_ids, test_ids = train_test_split(file_ids, train_size=0.8, random_state=13, shuffle=True)
len(train_dev_ids), len(test_ids)
train_dev_root = Path('/home/zehao.yu/workspace/py3/dr_ann/data/used/train_set')
test_root = Path('/home/zehao.yu/workspace/py3/dr_ann/data/used/test_set')
#create notes file
Path(train_dev_root).mkdir(parents=True, exist_ok=True)
Path(test_root).mkdir(parents=True, exist_ok=True)
train_root=Path(training_root)
#copy file to train and test
for fid in train_dev_ids:
    txt_fn = train_root / (fid + ".txt")
    ann_fn = train_root / (fid + ".ann")
    txt_fn1 = train_dev_root / (fid + ".txt")
    ann_fn1 = train_dev_root / (fid + ".ann")
    shutil.copyfile(txt_fn, txt_fn1)
    shutil.copyfile(ann_fn, ann_fn1)
for fid in test_ids:
    txt_fn = train_root / (fid + ".txt")
    ann_fn = train_root / (fid + ".ann")
    txt_fn1 = test_root / (fid + ".txt")
    ann_fn1 = test_root / (fid + ".ann")
    shutil.copyfile(txt_fn, txt_fn1)
    shutil.copyfile(ann_fn, ann_fn1)

In [12]:
#test_root = Path('/home/zehao.yu/workspace/py3/dr_ann/diabetic_retinopathy/test_set')
file_ids = set()
enss = []

for fn in test_root.glob("*.ann"):
    file_ids.add(fn.stem)
    _, ens, _ = read_annotation_brat(fn)
    enss.extend(ens)
print("test files: ", len(file_ids), list(file_ids)[:5])
print("total test eneitites: ", len(enss))
print("Entities distribution by types:\n", "\n".join([str(c) for c in Counter([each[1] for each in enss]).most_common()]))

test files:  145 ['note_7572', '2482683_note_7206', 'note_161', 'note_2248', 'note_6044']
total test eneitites:  1647
Entities distribution by types:
 ('lesion', 896)
('laterality', 485)
('severity', 249)
('eye_part', 17)


In [13]:
# Brief descriptive statistics for train
file_ids = set()
enss = []

for fn in train_dev_root.glob("*.ann"):
    file_ids.add(fn.stem)
    _, ens, _ = read_annotation_brat(fn)
    enss.extend(ens)
print("training files: ", len(file_ids), list(file_ids)[:5])
print("total training eneitites: ", len(enss))
print("Entities distribution by types:\n", "\n".join([str(c) for c in Counter([each[1] for each in enss]).most_common()]))

training files:  378 ['note_7515', 'note_7940', 'note_3006', 'note_3194', 'note_8106']
total training eneitites:  4287
Entities distribution by types:
 ('lesion', 2383)
('laterality', 1280)
('severity', 579)
('eye_part', 45)


In [14]:
# generate BIO from brat annotation
train_root = train_dev_root
train_bio = "/home/zehao.yu/workspace/py3/dr_ann/data/bio/trains/"

output_root = Path(train_bio)
output_root.mkdir(parents=True, exist_ok=True)

for fid in file_ids:
    txt_fn = train_root / (fid + ".txt")
    ann_fn = train_root / (fid + ".ann")
    bio_fn = output_root / (fid + ".bio.txt")
    
    txt, sents = pre_processing(txt_fn, deid_pattern=MIMICIII_PATTERN)
    e2idx, entities, rels = read_annotation_brat(ann_fn)
    nsents, sent_bound = generate_BIO(sents, entities, file_id=fid, no_overlap=False)
    #print(nsents)
    BIOdata_to_file(bio_fn, nsents)
    #break

2021-02-08 02:01:16,902 INFO sentence boundary detection class initiated.
2021-02-08 02:01:16,903 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:16,904 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_7515.txt ...
2021-02-08 02:01:16,922 INFO process note_7515 file
2021-02-08 02:01:17,018 INFO sentence boundary detection class initiated.
2021-02-08 02:01:17,019 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:17,020 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_7940.txt ...
2021-02-08 02:01:17,038 INFO process note_7940 file
2021-02-08 02:01:17,039 WARNING ('Active\xa0', 'severity', (1591, 1598)) offset is overlapped with previous entity; current tok not overlap
2021-02-08 02:01:17,109 INFO sentence boundary detection class initiated.
2021-02-08 02:01:17,109 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:17,110 INFO cur

2021-02-08 02:01:18,642 INFO process 87477_note_210 file
2021-02-08 02:01:18,693 INFO sentence boundary detection class initiated.
2021-02-08 02:01:18,694 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:18,695 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_2353.txt ...
2021-02-08 02:01:18,716 INFO process note_2353 file
2021-02-08 02:01:18,769 INFO sentence boundary detection class initiated.
2021-02-08 02:01:18,770 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:18,770 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_9242.txt ...
2021-02-08 02:01:18,781 INFO process note_9242 file
2021-02-08 02:01:18,849 INFO sentence boundary detection class initiated.
2021-02-08 02:01:18,850 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:18,850 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_4045.t

2021-02-08 02:01:20,416 INFO sentence boundary detection class initiated.
2021-02-08 02:01:20,417 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:20,418 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/2369330_note_6618.txt ...
2021-02-08 02:01:20,437 INFO process 2369330_note_6618 file
2021-02-08 02:01:20,488 INFO sentence boundary detection class initiated.
2021-02-08 02:01:20,489 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:20,489 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_8556.txt ...
2021-02-08 02:01:20,499 INFO process note_8556 file
2021-02-08 02:01:20,548 INFO sentence boundary detection class initiated.
2021-02-08 02:01:20,549 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:20,550 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/39541_note_166.txt ...
2021-02-08 02:01:20,560 INFO 

2021-02-08 02:01:22,189 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:22,189 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/1230653_note_2636.txt ...
2021-02-08 02:01:22,199 INFO process 1230653_note_2636 file
2021-02-08 02:01:22,249 INFO sentence boundary detection class initiated.
2021-02-08 02:01:22,250 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:22,250 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_7702.txt ...
2021-02-08 02:01:22,271 INFO process note_7702 file
2021-02-08 02:01:22,340 INFO sentence boundary detection class initiated.
2021-02-08 02:01:22,341 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:22,342 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_7933.txt ...
2021-02-08 02:01:22,352 INFO process note_7933 file
2021-02-08 02:01:22,404 INFO sentence boundary detection

2021-02-08 02:01:23,940 INFO process note_8524 file
2021-02-08 02:01:24,007 INFO sentence boundary detection class initiated.
2021-02-08 02:01:24,008 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:24,008 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_7788.txt ...
2021-02-08 02:01:24,018 INFO process note_7788 file
2021-02-08 02:01:24,068 INFO sentence boundary detection class initiated.
2021-02-08 02:01:24,069 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:24,070 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_1245.txt ...
2021-02-08 02:01:24,095 INFO process note_1245 file
2021-02-08 02:01:24,148 INFO sentence boundary detection class initiated.
2021-02-08 02:01:24,149 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:24,149 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/2748168_note_922

...

2021-02-08 02:01:36,196 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:36,196 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_8730.txt ...
2021-02-08 02:01:36,214 INFO process note_8730 file
2021-02-08 02:01:36,273 INFO sentence boundary detection class initiated.
2021-02-08 02:01:36,274 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:36,275 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/460233_note_1091.txt ...
2021-02-08 02:01:36,296 INFO process 460233_note_1091 file
2021-02-08 02:01:36,346 INFO sentence boundary detection class initiated.
2021-02-08 02:01:36,347 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:36,348 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/1816965_note_4518.txt ...
2021-02-08 02:01:36,358 INFO process 1816965_note_4518 file
2021-02-08 02:01:36,407 INFO sentence boun

2021-02-08 02:01:37,881 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:37,881 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/2583789_note_8208.txt ...
2021-02-08 02:01:37,901 INFO process 2583789_note_8208 file
2021-02-08 02:01:37,971 INFO sentence boundary detection class initiated.
2021-02-08 02:01:37,972 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:37,973 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_8700.txt ...
2021-02-08 02:01:37,984 INFO process note_8700 file
2021-02-08 02:01:38,035 INFO sentence boundary detection class initiated.
2021-02-08 02:01:38,036 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:38,037 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_7661.txt ...
2021-02-08 02:01:38,058 INFO process note_7661 file
2021-02-08 02:01:38,126 INFO sentence boundary detection

2021-02-08 02:01:39,562 INFO process note_4359 file
2021-02-08 02:01:39,611 INFO sentence boundary detection class initiated.
2021-02-08 02:01:39,612 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:39,612 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_70.txt ...
2021-02-08 02:01:39,638 INFO process note_70 file
2021-02-08 02:01:39,692 INFO sentence boundary detection class initiated.
2021-02-08 02:01:39,693 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:39,694 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_8554.txt ...
2021-02-08 02:01:39,705 INFO process note_8554 file
2021-02-08 02:01:39,773 INFO sentence boundary detection class initiated.
2021-02-08 02:01:39,774 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:39,775 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/2484779_note_7312.tx

2021-02-08 02:01:41,357 INFO sentence boundary detection class initiated.
2021-02-08 02:01:41,357 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:41,358 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/2678512_note_8911.txt ...
2021-02-08 02:01:41,367 INFO process 2678512_note_8911 file
2021-02-08 02:01:41,416 INFO sentence boundary detection class initiated.
2021-02-08 02:01:41,417 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:41,418 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_209.txt ...
2021-02-08 02:01:41,428 INFO process note_209 file
2021-02-08 02:01:41,480 INFO sentence boundary detection class initiated.
2021-02-08 02:01:41,481 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:41,482 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/1114244_note_1986.txt ...
2021-02-08 02:01:41,493 INFO

2021-02-08 02:01:43,082 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:43,082 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/note_6192.txt ...
2021-02-08 02:01:43,105 INFO process note_6192 file
2021-02-08 02:01:43,156 INFO sentence boundary detection class initiated.
2021-02-08 02:01:43,156 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:43,157 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/1647323_note_3946.txt ...
2021-02-08 02:01:43,166 INFO process 1647323_note_3946 file
2021-02-08 02:01:43,217 INFO sentence boundary detection class initiated.
2021-02-08 02:01:43,218 INFO word level tokenization with replace_number set to False
2021-02-08 02:01:43,218 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/train_set/217884_note_474.txt ...
2021-02-08 02:01:43,240 INFO process 217884_note_474 file
2021-02-08 02:01:43,291 INFO sentence bounda

In [15]:
# let us pick a file for check
! cat ./data/bio/trains/1737201_note_4194.bio.txt

OCT 0 3 0 3 O
, 3 4 4 5 O
Retina 5 11 6 12 O
- 12 13 13 14 O
OU 14 16 15 17 O
- 17 18 18 19 O
Both 19 23 20 24 B-laterality
Eyes 24 28 25 29 I-laterality
Without 33 40 30 37 O
IRF 41 44 38 41 B-lesion
/ 44 45 42 43 O
SRF 45 48 44 47 B-lesion
, 48 49 48 49 O
+ 50 51 50 51 O
RPED 51 55 52 56 O
OPH 60 63 57 60 O
- 64 65 61 62 O
OS 66 68 63 65 O
Intravitreal 69 81 66 78 O
Injection 82 91 79 88 O
, 91 92 89 90 O
Pharmacologic 93 106 91 104 O
Agent 107 112 105 110 O
Date 117 121 111 115 O
: 121 122 116 117 O
DATE 126 130 118 122 O
Patient 134 141 123 130 O
Name 142 146 131 135 O
: 146 147 136 137 O
NAME 151 155 138 142 O
Procedure 160 169 143 152 O
: 169 170 153 154 O
Intravitreal 171 183 155 167 O
Injection 184 193 168 177 O
, 193 194 178 179 O
OS 195 197 180 182 O
Intravitreal 199 211 183 195 O
Injection 212 221 196 205 O
Procedure 222 231 206 215 O
Note 232 236 216 220 O
Eye 238 241 221 224 O
: 241 242 225 226 O
OS 244 246 227 229 O
Pre 247 250 230 233 O
- 250 251 234 235 O
op 251 253 236

In [16]:
# now we have to split the train and dev sets
# for transformer NER, we need to name these two datasets as train.txt and dev.txt
file_ids = list(file_ids)
train_ids, dev_ids = train_test_split(file_ids, train_size=0.9, random_state=13, shuffle=True)
len(train_ids), len(dev_ids)

(340, 38)

In [17]:
# merge previous bio results into train.txt and dev.txt
import fileinput

# train
with open("./data/bio/train.txt", "w") as f:
    for fid in train_ids:
        f.writelines(fileinput.input(output_root / (fid + ".bio.txt")))
    fileinput.close()
        
# dev
with open("./data/bio/dev.txt", "w") as f:
    for fid in dev_ids:
        f.writelines(fileinput.input(output_root / (fid + ".bio.txt")))
    fileinput.close()
    
# now you can check your ./2018n2c2/bio, there should be two new files train.txt and dev.txt
! ls -l ./data/bio

total 3884
-rw-rw-r--. 1 zehao.yu zehao.yu  381223 Feb  8 02:01 dev.txt
drwxrwxr-x. 2 zehao.yu zehao.yu    4096 Feb  1 01:21 test
drwxrwxr-x. 2 zehao.yu zehao.yu   16384 Feb  8 02:01 trains
-rw-rw-r--. 1 zehao.yu zehao.yu 3566682 Feb  8 02:01 train.txt


In [18]:
! cat ./data/bio/train.txt

Visit 0 5 0 5 O
Date 6 10 6 10 O
: 10 11 11 12 O
9 13 14 13 14 O
/ 14 15 15 16 O
12 15 17 17 19 O
/ 17 18 21 22 O
2011 18 22 23 27 O
Chief 25 30 28 33 O
Complaint 31 40 34 43 O
: 40 41 44 45 O
Chief 42 47 46 51 O
Complaint 48 57 52 61 O
Patient 59 66 62 69 O
presents 67 75 70 78 O
with 76 80 79 83 O
• 82 83 84 85 O
Follow 84 90 86 92 O
- 90 91 93 94 O
up 91 93 95 97 O
h 97 98 98 99 O
/ 98 99 100 101 O
o 99 100 102 103 O
corneal 101 108 104 111 O
ulcer 109 114 112 117 O
Subjective 121 131 118 128 O
: 131 132 129 130 O
History 135 142 131 138 O
of 143 145 139 141 O
Present 146 153 142 149 O
Illness 154 161 150 157 O
: 161 162 158 159 O
Christopher 163 174 160 171 O
Walton 175 181 172 178 O
Demko 182 187 179 184 O
is 188 190 185 187 O
a 191 192 188 189 O
17 193 195 190 192 O
y 196 197 193 194 O
. 197 198 195 196 O
o 198 199 197 198 O
. 199 200 199 200 O
male 201 205 201 205 O
who 206 209 206 209 O
is 210 212 210 212 O
here 213 217 213 217 O
today 218 223 218 223 O
for 224 227 224 227 O
f 

27 2611 2613 2720 2722 O
/ 2613 2614 2723 2724 O
18 2614 2616 2725 2727 O
. 2616 2617 2728 2729 O

Now 2618 2621 2730 2733 O
improved 2622 2630 2734 2742 O
with 2631 2635 2743 2747 O
IVA 2636 2639 2748 2751 O
. 2639 2640 2752 2753 O

VA 2641 2643 2754 2756 O
20 2644 2646 2757 2759 O
/ 2646 2647 2760 2761 O
50 2647 2649 2762 2764 O
from 2650 2654 2765 2769 O
CF 2655 2657 2770 2772 O
in 2658 2660 2773 2775 O
Sept 2661 2665 2776 2780 O
. 2665 2666 2781 2782 O

Tx 2667 2669 2783 2785 O
on 2670 2672 2786 2788 O
11 2673 2675 2789 2791 O
/ 2675 2676 2792 2793 O
30 2676 2678 2794 2796 O
/ 2678 2679 2797 2798 O
18 2679 2681 2799 2801 O
with 2682 2686 2802 2806 O
final 2687 2692 2807 2812 O
dose 2693 2697 2813 2817 O
of 2698 2700 2818 2820 O
3 2701 2702 2821 2822 O
of 2703 2705 2823 2825 O
3 2706 2707 2826 2827 O
scheduled 2708 2717 2828 2837 O
injections 2718 2728 2838 2848 O
, 2728 2729 2849 2850 O
will 2730 2734 2851 2855 O
re 2735 2737 2856 2858 O
- 2737 2738 2859 2860 O
evaluate 2738 2746 2

and 1722 1725 1719 1722 O
Plan 1726 1730 1723 1727 O
: 1730 1731 1728 1729 O
ICD 1736 1739 1730 1733 O
- 1739 1740 1734 1735 O
10 1740 1742 1736 1738 O
- 1742 1743 1739 1740 O
CM 1743 1745 1741 1743 O
ICD 1746 1749 1744 1747 O
- 1749 1750 1748 1749 O
9 1750 1751 1750 1751 O
- 1751 1752 1752 1753 O
CM 1752 1754 1754 1756 O
1 1757 1758 1757 1758 O
. 1758 1759 1759 1760 O

Branch 1760 1766 1761 1767 O
retinal 1767 1774 1768 1775 O
vein 1775 1779 1776 1780 O
occlusion 1780 1789 1781 1790 O
with 1790 1794 1791 1795 O
macular 1795 1802 1796 1803 B-lesion
edema 1803 1808 1804 1809 I-lesion
of 1809 1811 1810 1812 O
left 1812 1816 1813 1817 B-laterality
eye 1817 1820 1818 1821 I-laterality
H34 1821 1824 1822 1825 O
. 1824 1825 1826 1827 O
8320 1825 1829 1828 1832 O
362.36 1830 1836 1833 1839 O
OCT 1837 1840 1840 1843 O
, 1840 1841 1844 1845 O
Posterior 1842 1851 1846 1855 O
Segment 1852 1859 1856 1863 O
- 1860 1861 1864 1865 O
OU 1862 1864 1866 1868 O
- 1865 1866 1869 1870 O
Both 1867 1871 1871

PH 507 509 526 528 O
20 510 512 529 531 O
/ 512 513 532 533 O
25 513 515 534 536 O
today 516 521 537 542 O
. 521 522 543 544 O

Monitor 523 530 545 552 O
OS 531 533 553 555 B-laterality
- 534 535 556 557 O
Severe 536 542 558 564 B-severity
NPDR 543 547 565 569 B-lesion
with 548 552 570 574 O
ciCSME 553 559 575 581 B-lesion
. 559 560 582 583 O

VA 561 563 584 586 O
PH 564 566 587 589 O
20 567 569 590 592 O
/ 569 570 593 594 O
20 570 572 595 597 O
. 572 573 598 599 O

OCT 574 577 600 603 O
with 578 582 604 608 O
subfoveal 583 592 609 618 O
IRF 593 596 619 622 O
stable 597 603 623 629 O
. 603 604 630 631 O

Given 605 610 632 637 O
vision 611 617 638 644 O
and 618 621 645 648 O
stability 622 631 649 658 O
will 632 636 659 663 O
monitor 637 644 664 671 O
. 644 645 672 673 O

2 649 650 676 677 O
) 650 651 678 679 O
Cataract 652 660 680 688 O
OU 661 663 689 691 O
- 664 665 692 693 O
mixed 666 671 694 699 O
OU 672 674 700 702 O
. 674 675 703 704 O

Rec 676 679 705 708 O
defer 680 685 709 714 O

marantic 4245 4253 4224 4232 O
endocarditis 4254 4266 4233 4245 O
. 4266 4267 4246 4247 O

Already 4268 4275 4248 4255 O
on 4276 4278 4256 4258 O
anticoagulation 4279 4294 4259 4274 O
( 4295 4296 4275 4276 O
warfarin 4296 4304 4277 4285 O
) 4304 4305 4286 4287 O
and 4306 4309 4288 4291 O
followed 4310 4318 4292 4300 O
with 4319 4323 4301 4305 O
cardiology 4324 4334 4306 4316 O
and 4335 4338 4317 4320 O
hematology 4339 4349 4321 4331 O
- 4351 4352 4332 4333 O
CTA 4353 4356 4334 4337 O
and 4357 4360 4338 4341 O
MRI 4361 4364 4342 4345 O
brain 4365 4370 4346 4351 O
already 4371 4378 4352 4359 O
ordered 4379 4386 4360 4367 O
by 4387 4389 4368 4370 O
neurology 4390 4399 4371 4380 O
, 4399 4400 4381 4382 O
pending 4401 4408 4383 4390 O
Return 4411 4417 4391 4397 O
to 4418 4420 4398 4400 O
clinic 4421 4427 4401 4407 O
: 4427 4428 4408 4409 O
Kathleen 4432 4440 4410 4418 O
Regan 4441 4446 4419 4424 O
, 4446 4447 4425 4426 O
MD 4448 4450 4427 4429 O
participated 4451 4463 4430 4442 O
in 4464 44

weeks 4492 4497 4648 4653 O
OCT 4498 4501 4654 4657 O
OU 4502 4504 4658 4660 O
, 4504 4505 4661 4662 O
IVL 4506 4509 4663 4666 O
OD 4510 4512 4667 4669 O
, 4512 4513 4670 4671 O
IVE 4514 4517 4672 4675 O
OS 4518 4520 4676 4678 O
Aaron 4522 4527 4679 4684 O
Noll 4528 4532 4685 4689 O
, 4532 4533 4690 4691 O
MD 4534 4536 4692 4694 O
participated 4537 4549 4695 4707 O
in 4550 4552 4708 4710 O
the 4553 4556 4711 4714 O
care 4557 4561 4715 4719 O
of 4562 4564 4720 4722 O
this 4565 4569 4723 4727 O
patient 4570 4577 4728 4735 O
. 4577 4578 4736 4737 O

Siva 4579 4583 4738 4742 O
S 4584 4585 4743 4744 O
. 4585 4586 4745 4746 O
R 4586 4587 4747 4748 O
. 4587 4588 4749 4750 O
Iyer 4589 4593 4751 4755 O
, 4593 4594 4756 4757 O
MD 4595 4597 4758 4760 O
I 4599 4600 4761 4762 O
have 4601 4605 4763 4767 O
seen 4606 4610 4768 4772 O
and 4611 4614 4773 4776 O
examined 4615 4623 4777 4785 O
this 4624 4628 4786 4790 O
patient 4629 4636 4791 4798 O
. 4636 4637 4799 4800 O

I 4638 4639 4801 4802 O
have 46

OS 3963 3965 3946 3948 B-laterality
with 3966 3970 3949 3953 O
increased 3971 3980 3954 3963 O
subretinal 3981 3991 3964 3974 O
fibrosis 3992 4000 3975 3983 O
and 4001 4004 3984 3987 O
pockets 4005 4012 3988 3995 O
of 4013 4015 3996 3998 O
SRF 4016 4019 3999 4002 B-lesion
. 4019 4020 4003 4004 O

EYlea 4021 4026 4005 4010 O
OU 4027 4029 4011 4013 O
today 4030 4035 4014 4019 O
. 4035 4036 4020 4021 O

3 4037 4038 4022 4023 O
) 4038 4039 4024 4025 O
history 4040 4047 4026 4033 O
of 4048 4050 4034 4036 O
steroid 4051 4058 4037 4044 O
induced 4059 4066 4045 4052 O
ocular 4067 4073 4053 4059 O
HTN 4074 4077 4060 4063 O
: 4077 4078 4064 4065 O
- 4080 4081 4066 4067 O
excellent 4081 4090 4068 4077 O
low 4091 4094 4078 4081 O
- 4094 4095 4082 4083 O
normal 4095 4101 4084 4090 O
IOP 4102 4105 4091 4094 O
of 4106 4108 4095 4097 O
10 4109 4111 4098 4100 O
, 4111 4112 4101 4102 O
11 4112 4114 4103 4105 O
today 4115 4120 4106 4111 O
on 4121 4123 4112 4114 O
max 4124 4127 4115 4118 O
med 4128 4131 4

disorders 199 208 176 185 O
referred 209 217 186 194 O
for 218 221 195 198 O
diplopia 222 230 199 207 O
on 231 233 208 210 O
exam 234 238 211 215 O
with 239 243 216 220 O
them 244 248 221 225 O
. 248 249 226 227 O

Pt 250 252 228 230 O
notes 253 258 231 236 O
difficulty 259 269 237 247 O
when 270 274 248 252 O
looking 275 282 253 260 O
up 283 285 261 263 O
close 286 291 264 269 O
at 292 294 270 272 O
phone 295 300 273 278 O
etc 301 304 279 282 O
. 304 305 283 284 O

Says 306 310 285 289 O
not 311 314 290 293 O
true 315 319 294 298 O
doubling 320 328 299 307 O
but 329 332 308 311 O
blurry 333 339 312 318 O
. 339 340 319 320 O

Last 346 350 321 325 O
edited 351 357 326 332 O
by 358 360 333 335 O
NAME 364 368 336 340 O
on 372 374 341 343 O
DATE 378 382 344 348 O
3 387 388 349 350 O
: 388 389 351 352 O
30 389 391 353 355 O
PM 392 394 356 358 O
. 394 395 359 360 O

Patient 400 407 361 368 O
Active 408 414 369 375 O
Problem 415 422 376 383 O
List 423 427 384 388 O
Diagnosis 430 439 389 398 O

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [25]:
os.environ['MKL_NUM_THREADS'] = '1'

# Train model

In [1]:
"""
Next we will train the NER model
We will just use a BERT model pre-trained on general English corpora as an example

In general we need GPU to train the model, running with CPU the training will be extremely slow. 
We just give an demo here.  You can train you own model when you have GPU resources.

To use GPU, you just need to run 'export CUDA_VISIBLE_DEVICES=0' before run the training command
"""
#! MKL_THREADING_LAYER=GNU
! export CUDA_VISIBLE_DEVICES=0  # indicate no GPU; if you have two GPUs then the IDs for them will be 0 and 1

! MKL_THREADING_LAYER=GNU python ./ClinicalTransformerNER/src/run_transformer_ner.py \
      --model_type roberta \
      --pretrained_model roberta-base \
      --data_dir ./data/bio \
      --new_model_dir ./new_saved_models/roberta_2 \
      --overwrite_model_dir \
      --max_seq_length 128 \
      --data_has_offset_information \
      --save_model_core \
      --do_train \
      --model_selection_scoring strict-f_score-1 \
      --do_lower_case \
      --train_batch_size 8 \
      --train_steps 1000 \
      --learning_rate 1e-5 \
      --num_train_epochs 30 \
      --gradient_accumulation_steps 1 \
      --do_warmup \
      --seed 15 \
      --warmup_ratio 0.1 \
      --max_num_checkpoints 3 \
      --log_file ./log_roberta.txt \
      --progress_bar \
      --early_stop 8 

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaNerModel: ['lm_head.bias', 'lm_head.dense.weight', 'lm_head.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.layer_norm.bias', 'lm_head.decoder.weight']
- This IS expected if you are initializing RobertaNerModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaNerModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaNerModel were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
^C


In [ ]:
#roberta test
python ./ClinicalTransformerNER/src/run_transformer_ner.py \
      --model_type roberta \
      --pretrained_model roberta-base \
      --data_dir ./data/bio \
      --new_model_dir ./new_saved_models/roberta_test \
      --overwrite_model_dir \
      --max_seq_length 128 \
      --data_has_offset_information \
      --save_model_core \
      --do_train \
      --model_selection_scoring strict-f_score-1 \
      --do_lower_case \
      --train_batch_size 8 \
      --train_steps 1000 \
      --learning_rate 1e-5 \
      --num_train_epochs 30 \
      --gradient_accumulation_steps 1 \
      --do_warmup \
      --seed 13 \
      --warmup_ratio 0.1 \
      --max_num_checkpoints 3 \
      --log_file ./log_roberta_test.txt \
      --progress_bar \
      --early_stop 8 

In [1]:
! pwd

/home/zehao.yu/workspace/py3/dr_ann


In [ ]:
#roberta mimic
python ./ClinicalTransformerNER/src/run_transformer_ner.py \
      --model_type roberta \
      --pretrained_model ./pre_train_model/mimiciii_roberta_10e_128b \
      --data_dir ./data/bio \
      --new_model_dir ./new_saved_models/roberta_mimic \
      --overwrite_model_dir \
      --max_seq_length 128 \
      --data_has_offset_information \
      --save_model_core \
      --do_train \
      --model_selection_scoring strict-f_score-1 \
      --do_lower_case \
      --train_batch_size 8 \
      --train_steps 1000 \
      --learning_rate 1e-5 \
      --num_train_epochs 30 \
      --gradient_accumulation_steps 1 \
      --do_warmup \
      --seed 13 \
      --warmup_ratio 0.1 \
      --max_num_checkpoints 3 \
      --log_file ./log_roberta_mimic.txt \
      --progress_bar \
      --early_stop 8 

In [ ]:
python ./ClinicalTransformerNER/src/run_transformer_ner.py \
      --model_type bert \
      --pretrained_model ./pre_train_model/mimiciii_bert_10e_128b \
      --data_dir ./data/bio \
      --new_model_dir ./new_saved_models/bert_mimic \
      --overwrite_model_dir \
      --max_seq_length 128 \
      --data_has_offset_information \
      --save_model_core \
      --do_train \
      --model_selection_scoring strict-f_score-1 \
      --do_lower_case \
      --train_batch_size 8 \
      --train_steps 1000 \
      --learning_rate 1e-5 \
      --num_train_epochs 30 \
      --gradient_accumulation_steps 1 \
      --do_warmup \
      --seed 13 \
      --warmup_ratio 0.1 \
      --max_num_checkpoints 3 \
      --log_file ./log_roberta_mimic.txt \
      --progress_bar \
      --early_stop 8 

In [20]:
! ls -l ./new_saved_models/bert

total 1711384
-rw-rw-r--. 1 zehao.yu zehao.yu        17 Jan 25 01:07 added_tokens.json
-rw-rw-r--. 1 zehao.yu zehao.yu       101 Jan 25 00:52 base_model_name.txt
-rw-rw-r--. 1 zehao.yu zehao.yu 438058313 Jan 25 00:57 checkpoint_1999.bin
-rw-rw-r--. 1 zehao.yu zehao.yu 438058313 Jan 25 00:59 checkpoint_2999.bin
-rw-rw-r--. 1 zehao.yu zehao.yu 438058313 Jan 25 01:01 checkpoint_3999.bin
-rw-rw-r--. 1 zehao.yu zehao.yu      1229 Jan 25 01:07 config.json
-rw-rw-r--. 1 zehao.yu zehao.yu       174 Jan 25 00:52 label2idx.json
-rw-rw-r--. 1 zehao.yu zehao.yu 438018551 Jan 25 01:01 pytorch_model.bin
-rw-rw-r--. 1 zehao.yu zehao.yu       112 Jan 25 01:07 special_tokens_map.json
-rw-rw-r--. 1 zehao.yu zehao.yu        48 Jan 25 01:07 tokenizer_config.json
-rw-rw-r--. 1 zehao.yu zehao.yu    231508 Jan 25 01:07 vocab.txt


# Prediction

In [19]:
"""
running prediction

In our transformer package, we have the format conversion between bio and brat; bioc implemented
"""

# generate bio
#test_root = Path('/home/zehao.yu/workspace/py3/dr_ann/diabetic_retinopathy/test_set_les')
test_bio = "/home/zehao.yu/workspace/py3/dr_ann/data/bio/test/"
output_root = Path(test_bio)
output_root.mkdir(parents=True, exist_ok=True)

for fn in test_root.glob("*.txt"):
    txt_fn = fn
    bio_fn = output_root / (fn.stem + ".bio.txt")
    
    txt, sents = pre_processing(txt_fn, deid_pattern=MIMICIII_PATTERN)
    nsents, sent_bound = generate_BIO(sents, [], file_id=fid, no_overlap=False)
    
    BIOdata_to_file(bio_fn, nsents)

2021-02-08 02:12:42,819 INFO sentence boundary detection class initiated.
2021-02-08 02:12:42,819 INFO word level tokenization with replace_number set to False
2021-02-08 02:12:42,820 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_7357.txt ...
2021-02-08 02:12:42,850 INFO process note_2063 file
2021-02-08 02:12:42,963 INFO sentence boundary detection class initiated.
2021-02-08 02:12:42,978 INFO word level tokenization with replace_number set to False
2021-02-08 02:12:42,979 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/876827_note_1263.txt ...
2021-02-08 02:12:43,010 INFO process note_2063 file
2021-02-08 02:12:43,063 INFO sentence boundary detection class initiated.
2021-02-08 02:12:43,064 INFO word level tokenization with replace_number set to False
2021-02-08 02:12:43,065 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_439.txt ...
2021-02-08 02:12:43,076 INFO process note_2063 

2021-02-08 02:12:44,669 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_7729.txt ...
2021-02-08 02:12:44,686 INFO process note_2063 file
2021-02-08 02:12:44,783 INFO sentence boundary detection class initiated.
2021-02-08 02:12:44,796 INFO word level tokenization with replace_number set to False
2021-02-08 02:12:44,797 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_7788.txt ...
2021-02-08 02:12:44,806 INFO process note_2063 file
2021-02-08 02:12:44,856 INFO sentence boundary detection class initiated.
2021-02-08 02:12:44,857 INFO word level tokenization with replace_number set to False
2021-02-08 02:12:44,858 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_6281.txt ...
2021-02-08 02:12:44,877 INFO process note_2063 file
2021-02-08 02:12:44,928 INFO sentence boundary detection class initiated.
2021-02-08 02:12:44,929 INFO word level tokenization with replace_number set to False
2

2021-02-08 02:12:46,464 INFO sentence boundary detection class initiated.
2021-02-08 02:12:46,465 INFO word level tokenization with replace_number set to False
2021-02-08 02:12:46,465 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_7753.txt ...
2021-02-08 02:12:46,480 INFO process note_2063 file
2021-02-08 02:12:46,541 INFO sentence boundary detection class initiated.
2021-02-08 02:12:46,541 INFO word level tokenization with replace_number set to False
2021-02-08 02:12:46,542 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/2253176_note_6203.txt ...
2021-02-08 02:12:46,554 INFO process note_2063 file
2021-02-08 02:12:46,627 INFO sentence boundary detection class initiated.
2021-02-08 02:12:46,643 INFO word level tokenization with replace_number set to False
2021-02-08 02:12:46,644 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_8649.txt ...
2021-02-08 02:12:46,654 INFO process note_206

2021-02-08 02:12:48,222 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/1590841_note_3799.txt ...
2021-02-08 02:12:48,232 INFO process note_2063 file
2021-02-08 02:12:48,282 INFO sentence boundary detection class initiated.
2021-02-08 02:12:48,283 INFO word level tokenization with replace_number set to False
2021-02-08 02:12:48,283 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/1896876_note_5099.txt ...
2021-02-08 02:12:48,292 INFO process note_2063 file
2021-02-08 02:12:48,344 INFO sentence boundary detection class initiated.
2021-02-08 02:12:48,345 INFO word level tokenization with replace_number set to False
2021-02-08 02:12:48,345 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_3174.txt ...
2021-02-08 02:12:48,353 INFO process note_2063 file
2021-02-08 02:12:48,444 INFO sentence boundary detection class initiated.
2021-02-08 02:12:48,444 INFO word level tokenization with replace_numbe

2021-02-08 02:12:49,898 INFO process note_2063 file
2021-02-08 02:12:49,950 INFO sentence boundary detection class initiated.
2021-02-08 02:12:49,951 INFO word level tokenization with replace_number set to False
2021-02-08 02:12:49,952 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_7563.txt ...
2021-02-08 02:12:49,978 INFO process note_2063 file
2021-02-08 02:12:50,039 INFO sentence boundary detection class initiated.
2021-02-08 02:12:50,040 INFO word level tokenization with replace_number set to False
2021-02-08 02:12:50,040 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_5975.txt ...
2021-02-08 02:12:50,051 INFO process note_2063 file
2021-02-08 02:12:50,100 INFO sentence boundary detection class initiated.
2021-02-08 02:12:50,101 INFO word level tokenization with replace_number set to False
2021-02-08 02:12:50,102 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/2183623_note_6078.t

2021-02-08 02:12:51,762 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/note_5983.txt ...
2021-02-08 02:12:51,771 INFO process note_2063 file
2021-02-08 02:12:51,820 INFO sentence boundary detection class initiated.
2021-02-08 02:12:51,821 INFO word level tokenization with replace_number set to False
2021-02-08 02:12:51,821 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/1342474_note_3109.txt ...
2021-02-08 02:12:51,831 INFO process note_2063 file
2021-02-08 02:12:51,895 INFO sentence boundary detection class initiated.
2021-02-08 02:12:51,896 INFO word level tokenization with replace_number set to False
2021-02-08 02:12:51,897 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set/217884_note_474.txt ...
2021-02-08 02:12:51,919 INFO process note_2063 file
2021-02-08 02:12:51,971 INFO sentence boundary detection class initiated.
2021-02-08 02:12:51,972 INFO word level tokenization with replace_number 

In [20]:

! export CUDA_VISIBLE_DEVICES=1

# use format 1 for BRAT, 2 for BioC, 0 as default for BIO
! MKL_THREADING_LAYER=GNU python ./ClinicalTransformerNER/src/run_transformer_batch_prediction.py \
      --model_type bert \
      --pretrained_model ./new_saved_models/bert \
      --raw_text_dir /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set \
      --preprocessed_text_dir /home/zehao.yu/workspace/py3/dr_ann/data/bio/test/ \
      --output_dir ./result/bert_result \
      --max_seq_length 128 \
      --do_lower_case \
      --eval_batch_size 8 \
      --log_file ./log_bert.txt\
      --do_format 1 \
      --do_copy \
      --data_has_offset_information

In [ ]:
#bert mimic
python ./ClinicalTransformerNER/src/run_transformer_batch_prediction.py \
      --model_type bert \
      --pretrained_model ./new_saved_models/bert_mimic \
      --raw_text_dir /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set \
      --preprocessed_text_dir /home/zehao.yu/workspace/py3/dr_ann/data/bio/test/ \
      --output_dir ./result/bert_mimic_result \
      --max_seq_length 128 \
      --do_lower_case \
      --eval_batch_size 8 \
      --log_file ./log_bert_mimic.txt\
      --do_format 1 \
      --do_copy \
      --data_has_offset_information

In [ ]:
#roberta
python ./ClinicalTransformerNER/src/run_transformer_batch_prediction.py \
      --model_type roberta \
      --pretrained_model ./new_saved_models/roberta_test \
      --raw_text_dir /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set \
      --preprocessed_text_dir /home/zehao.yu/workspace/py3/dr_ann/data/bio/test/ \
      --output_dir ./result/roberta_result_test \
      --max_seq_length 128 \
      --do_lower_case \
      --eval_batch_size 8 \
      --log_file ./log_roberta_test.txt\
      --do_format 1 \
      --do_copy \
      --data_has_offset_information

In [ ]:
#roberta mimic
python ./ClinicalTransformerNER/src/run_transformer_batch_prediction.py \
      --model_type roberta \
      --pretrained_model ./new_saved_models/roberta_mimic \
      --raw_text_dir /home/zehao.yu/workspace/py3/dr_ann/data/used/test_set \
      --preprocessed_text_dir /home/zehao.yu/workspace/py3/dr_ann/data/bio/test/ \
      --output_dir ./result/roberta_mimic_result \
      --max_seq_length 128 \
      --do_lower_case \
      --eval_batch_size 8 \
      --log_file ./log_roberta_mimic.txt\
      --do_format 1 \
      --do_copy \
      --data_has_offset_information

In [26]:
cat ./log_roberta.txt

2021-02-08 02:31:43 - Transformer_NER - INFO - Task will use cuda device: GPU_0.
2021-02-08 02:31:43 - Transformer_NER - WARNING - set tokenizer as roberta-base
2021-02-08 02:31:43 - Transformer_NER - WARNING - set config as roberta-base
2021-02-08 02:31:43 - Transformer_NER - INFO - Training/evaluation parameters: {'model_type': 'roberta', 'pretrained_model': 'roberta-base', 'config_name': 'roberta-base', 'tokenizer_name': 'roberta-base', 'data_dir': './data/bio', 'data_has_offset_information': True, 'new_model_dir': './new_saved_models/roberta', 'save_model_core': True, 'predict_output_file': None, 'overwrite_model_dir': True, 'seed': 13, 'max_seq_length': 128, 'do_train': True, 'model_selection_scoring': 'strict-f_score-1', 'do_predict': False, 'use_crf': False, 'do_lower_case': True, 'train_batch_size': 8, 'eval_batch_size': 8, 'train_steps': 1000, 'learning_rate': 1e-05, 'num_train_epochs': 30.0, 'gradient_accumulation_steps': 1, 'do_warmup': True, 'warmup_ratio': 0.1, 'weight_dec

input ids: [0, 14230, 1885, 90, 6204, 34194, 36, 13895, 448, 4839, 9, 314, 2295, 289, 2022, 479, 41717, 2491, 176, 4, 4419, 12471, 347, 3721, 1691, 4832, 33885, 2156, 9944, 1243, 111, 38923, 111, 1868, 26945, 155, 479, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]
label: [1, 3, 2, 2, 2, 3, 3, 3, 2, 3, 3, 3, 3, 3, 2, 3, 3, 3, 2, 2, 2, 3, 2, 2, 2, 3, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 3, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
mask: [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1

segment ids: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
guards: [0, 1, 1, 1, 2, 3, 3, 3, 4, 5, 6, 6, 7, 8, 9, 9, 9, 9, 10, 11, 12, 12, 13, 13, 14, 15, 16, 17, 18, 19, 20, 20, 21, 22, 23, 24, 25, 26, 27, 27, 27, 27, 28, 29, 29, 29, 29, 30, 31, 32, 33, 34, 35, 36, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
***********************************
            
2021-02-09 17:56:29 - Transformer_NER - INFO - 
************** Example ************
input tokens: ['<s>', 'ĠCar', 'ot', 'id'

input tokens: ['<s>', 'ĠAtt', 'ending', 'ĠNote', 'Ġ:', 'ĠTreatment', 'ĠH', 'x', 'Ġ:', 'ĠIV', 'FA', 'Ġ(', 'Ġtoday', 'Ġ)', 'Ġ:', 'Ġmid', 'per', 'ipher', 'al', 'Ġis', 'chem', 'ia', 'Ġ,', 'ĠNV', 'Ġ,', 'Ġmac', 'ular', 'Ġst', 'aining', 'Ġwith', 'Ġleakage', 'ĠU', 've', 'itic', 'Ġwork', 'up', 'Ġ(', 'Ġordered', 'ĠD', 'ATE', 'Ġ)', 'ĠAce', 'Ġ66', 'Ġ(', 'ĠBorder', 'line', 'Ġ)', 'ĠLy', 'so', 'zyme', 'Ġ7', '.', '4', 'Ġ(', 'Ġw', 'nl', 'Ġ)', 'ĠChest', 'ĠX', 'Ġ-', 'ĠRay', 'Ġw', 'nl', 'ĠTB', 'Ġ(', 'ĠP', 'PD', 'Ġand', 'ĠQuan', 'ter', 'fer', 'on', 'Ġ)', 'ĠN', 'EG', 'ĠSy', 'philis', 'Ġ(', 'ĠR', 'PR', 'Ġand', 'ĠFTA', 'Ġ-', 'ĠAB', 's', 'Ġ)', 'ĠNR', 'ĠHIV', 'ĠN', 'EG', 'ĠT', 'ox', 'opl', 'asm', 'osis', 'ĠIg', 'G', 'Ġw', 'nl', 'Ġ,', 'ĠIg', 'M', 'ĠN', 'EG', 'ĠANC', 'As', 'Ġw', 'nl', 'ĠLyme', 'ĠN', 'EG', 'Ġ1', 'Ġ)', 'ĠRet', 'in', 'itis', 'Ġ/', 'ĠRet', 'in', 'opathy', 'ĠOU', 'Ġ-', 'Ġpresented', 'Ġas', 'Ġa', 'Ġreferral', '[next]', '</s>']
input ids: [0, 7279, 4345, 6068, 4832, 19120, 289, 1178, 4832, 10831, 5944, 

mask: [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]
segment ids: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
guards: [0, 1, 2, 3, 3, 4, 4, 5, 6, 7, 8, 9, 10, 10, 11, 12, 13, 14, 14, 15, 16, 17, 17, 17, 17, 18, 18, 19, 20, 20, 21, 22, 23, 24, 24, 25, 26, 27, 28, 29, 30, 31, 31, 31, 31, 32, 32, 33, 34, 35, 35, 35, 35, 36

input tokens: ['<s>', 'ĠZ', '98', 'Ġ.', 'Ġ8', '90', 'ĠV', '45', 'Ġ.', 'Ġ69', 'ĠPOW', 'Ġ#', 'Ġ1', 'ĠS', 'Ġ/', 'ĠP', 'Ġ25', 'Ġg', 'ĠPP', 'V', 'Ġ/', 'ĠML', 'Ġ/', 'ĠSc', 'issors', 'ĠSD', 'EM', 'Ġ/', 'Ġwith', 'Ch', 'andel', 'ier', 'Ġ/', 'ĠAF', 'x', 'Ġ/', 'ĠEL', 'Ġ/', 'ĠSO', 'Ġ/', 'ĠST', 'ĠTri', 'am', 'cin', 'ol', 'one', 'ĠOD', 'Ġ8', 'Ġ/', 'Ġ13', 'Ġ/', 'Ġ18', 'Ġ.', '</s>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [27]:
cat ./log_roberta_mimic.txt

2021-02-09 15:03:35 - Transformer_NER - INFO - Task will use cuda device: GPU_0.
2021-02-09 15:03:35 - Transformer_NER - WARNING - set tokenizer as ./pre_train_model/mimiciii_roberta_10e_128b
2021-02-09 15:03:35 - Transformer_NER - WARNING - set config as ./pre_train_model/mimiciii_roberta_10e_128b
2021-02-09 15:03:35 - Transformer_NER - INFO - Training/evaluation parameters: {'model_type': 'roberta', 'pretrained_model': './pre_train_model/mimiciii_roberta_10e_128b', 'config_name': './pre_train_model/mimiciii_roberta_10e_128b', 'tokenizer_name': './pre_train_model/mimiciii_roberta_10e_128b', 'data_dir': './data/bio', 'data_has_offset_information': True, 'new_model_dir': './new_saved_models/roberta_mimic', 'save_model_core': True, 'predict_output_file': None, 'overwrite_model_dir': True, 'seed': 13, 'max_seq_length': 128, 'do_train': True, 'model_selection_scoring': 'strict-f_score-1', 'do_predict': False, 'use_crf': False, 'do_lower_case': True, 'train_batch_size': 8, 'eval_batch_size'

Recent renal function decline , and lung mass being evaluated for possible CA . Treatment History IVA OU - 8 / 31 / 18 ( today ) IVA OU - 7 / 22 / 18 IVA OU - 6 / 15 / 18 IVA OU - 5 / 11 / 18 IVA OU - 4 / 6 / 18 IVA OU - 3 / 2 / 18 IVA OU - 1 / 26 / 17 IVA OU - 12 / 15 / 17 IVA OU - 11 / 9 / 17 IVA OU - 10 / 6 / 17 IVA OS - 7 / 20 / 2017 IVA OS - 6 / 13 / 2017 IVA OU - Kay ( 4 / 7 / 17 ) Intravitreal injection OU ( with Dr. Kay , April 2017 ) 1 ) IDDM - [ Dx 2002 , A 1 C 6.9 ] Moderate NPDR with ciCSME OU OD - ciCSME has responded to IVA but now plateau / stable OS - ciCSME has responded to IVA , but now plateau / stable Plateau response to IVA , would like to switch to Lucentis but not covered by FAP , will continue IVA . 2 ) NSC OU - 20 / 50 and 20 / 40 .

2021-02-09 17:09:51 - Transformer_NER - WARNING - 
Sentence after tokenization is too long (expect less than 126 but got 178).
You have to increase max_seq_length to make sure every sentence after tokenization is not longer than th

2021-02-09 17:57:32 - Transformer_NER - WARNING - The output file is ./result/roberta_mimic_result/2542462_note_7938.bio.txt, we recommend to use suffix as .bio.txt or .txt. 
            You can directly use formatter coverter tool in this package.
2021-02-09 17:57:32 - Transformer_NER - INFO - 
************** Example ************
input tokens: ['<s>', 'ĠAssessment', 'Ġand', 'ĠPlan', 'Ġ:', 'ĠI', 'CD', 'Ġ-', 'Ġ10', 'Ġ-', 'ĠCM', 'ĠI', 'CD', 'Ġ-', 'Ġ9', 'Ġ-', 'ĠCM', 'Ġ1', 'Ġ.', '</s>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>',

input ids: [0, 208, 1589, 221, 18390, 846, 885, 1589, 18592, 35231, 10373, 22907, 927, 1499, 8192, 14722, 1589, 14722, 1589, 504, 525, 5208, 479, 290, 3248, 468, 1898, 479, 5913, 19120, 7298, 18390, 846, 1589, 38, 3384, 16161, 927, 1258, 8192, 111, 204, 1589, 204, 1589, 504, 14422, 4729, 510, 38923, 112, 4839, 211, 13714, 23283, 38, 3384, 8192, 111, 221, 7111, 849, 112, 579, 1589, 181, 18390, 846, 19, 38, 3384, 7129, 479, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]
label: [1, 3, 3, 3, 3, 2, 3, 3, 3, 2, 3, 3, 2, 2, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 2, 3, 2, 3, 3, 3, 3, 3, 2, 3, 3, 2, 3, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 3, 3, 2, 2, 3, 2, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 2, 3, 3, 2, 3, 3, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
mask: [1, 1, 1, 1

2021-02-09 17:57:39 - Transformer_NER - WARNING - The output file is ./result/roberta_mimic_result/note_6192.bio.txt, we recommend to use suffix as .bio.txt or .txt. 
            You can directly use formatter coverter tool in this package.
2021-02-09 17:57:39 - Transformer_NER - INFO - 
************** Example ************
input tokens: ['<s>', 'ĠAssessment', 'Ġand', 'ĠPlan', 'Ġ:', 'ĠI', 'CD', 'Ġ-', 'Ġ10', 'Ġ-', 'ĠCM', 'ĠI', 'CD', 'Ġ-', 'Ġ9', 'Ġ-', 'ĠCM', 'Ġ1', 'Ġ.', '</s>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>', '<pad>'

mask: [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
segment ids: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
guards: [0, 1, 2, 3, 4, 5, 5, 6, 7, 8, 9, 10, 10, 11, 12, 13, 14, 15, 16, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



# result

In [20]:
#bert
! python brat_eval.py --f1 ./data/used/test_set --f2 ./result/bert_result_formatted_output/

******************* Information Extraction Results *******************
                      ------- strict -------    ------ lenient -------
                      Prec.   Rec.    F(b=1)    Prec.   Rec.    F(b=1)
              Lesion  0.9183  0.9654  0.9412    0.9382  0.9833  0.9602
            Severity  0.8778  0.9518  0.9133    0.8955  0.9639  0.9284
            Eye_part  0.3571  0.5882  0.4444    0.4074  0.6471  0.5000
          Laterality  0.8692  0.9588  0.9118    0.8822  0.9732  0.9255
                      ------------------------------------------------
     Overall (micro)  0.8885  0.9575  0.9217    0.9067  0.9739  0.9391
     Overall (macro)  0.8455  0.8909  0.8610    0.8650  0.9179  0.8818

***************************** RELATIONS ******************************
             located  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
     severity-lesion  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
   laterality-lesion  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
     

In [21]:
! python brat_eval.py --f1 ./data/used/test_set --f2 ./result/bert_mimic_result_formatted_output/

******************* Information Extraction Results *******************
                      ------- strict -------    ------ lenient -------
                      Prec.   Rec.    F(b=1)    Prec.   Rec.    F(b=1)
              Lesion  0.9555  0.9576  0.9565    0.9776  0.9743  0.9760
            Severity  0.9627  0.9317  0.9469    0.9668  0.9357  0.9510
            Eye_part  0.8000  0.7059  0.7500    0.8000  0.7059  0.7500
          Laterality  0.9339  0.9608  0.9472    0.9439  0.9711  0.9573
                      ------------------------------------------------
     Overall (micro)  0.9486  0.9520  0.9503    0.9642  0.9648  0.9645
     Overall (macro)  0.8908  0.8838  0.8836    0.9125  0.9062  0.9056

***************************** RELATIONS ******************************
             located  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
     severity-lesion  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
   laterality-lesion  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
     

In [28]:
! python brat_eval.py --f1 ./data/used/test_set --f2 ./result/roberta_result_formatted_output/

******************* Information Extraction Results *******************
                      ------- strict -------    ------ lenient -------
                      Prec.   Rec.    F(b=1)    Prec.   Rec.    F(b=1)
              Lesion  0.9414  0.9676  0.9543    0.9533  0.9788  0.9659
            Severity  0.9405  0.9518  0.9461    0.9444  0.9558  0.9501
            Eye_part  0.5500  0.6471  0.5946    0.5500  0.6471  0.5946
          Laterality  0.9025  0.9732  0.9365    0.9140  0.9856  0.9484
                      ------------------------------------------------
     Overall (micro)  0.9248  0.9636  0.9438    0.9353  0.9739  0.9542
     Overall (macro)  0.8726  0.8956  0.8793    0.8830  0.9125  0.8905

***************************** RELATIONS ******************************
             located  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
     severity-lesion  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
   laterality-lesion  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
     

In [24]:
! python brat_eval.py --f1 ./data/used/test_set --f2 ./result/roberta_mimic_result_formatted_output/

******************* Information Extraction Results *******************
                      ------- strict -------    ------ lenient -------
                      Prec.   Rec.    F(b=1)    Prec.   Rec.    F(b=1)
              Lesion  0.9565  0.9576  0.9571    0.9688  0.9688  0.9688
            Eye_part  0.7222  0.7647  0.7429    0.7222  0.7647  0.7429
            Severity  0.9440  0.9478  0.9459    0.9480  0.9518  0.9499
          Laterality  0.9137  0.9608  0.9367    0.9255  0.9732  0.9487
                      ------------------------------------------------
     Overall (micro)  0.9391  0.9551  0.9470    0.9498  0.9654  0.9575
     Overall (macro)  0.8800  0.8850  0.8771    0.8943  0.9069  0.8929

***************************** RELATIONS ******************************
             located  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
     severity-lesion  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
   laterality-lesion  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
     

In [29]:
! python brat_eval.py --f1 ./data/used/test_set --f2 ./result/roberta_result_test_formatted_output/

******************* Information Extraction Results *******************
                      ------- strict -------    ------ lenient -------
                      Prec.   Rec.    F(b=1)    Prec.   Rec.    F(b=1)
              Lesion  0.8881  0.9565  0.9210    0.9114  0.9754  0.9423
            Eye_part  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
            Severity  0.8100  0.9076  0.8561    0.8400  0.9277  0.8817
          Laterality  0.8259  0.9588  0.8874    0.8366  0.9711  0.8989
                      ------------------------------------------------
     Overall (micro)  0.8567  0.9399  0.8964    0.8770  0.9569  0.9152
     Overall (macro)  0.7982  0.8493  0.8129    0.8155  0.8714  0.8309

***************************** RELATIONS ******************************
             located  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
     severity-lesion  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
   laterality-lesion  0.0000  0.0000  0.0000    0.0000  0.0000  0.0000
     

# new round

In [24]:
# generate bio
test_root = Path('/home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/')
test_bio = "./data/bio_new/"
output_root = Path(test_bio)
output_root.mkdir(parents=True, exist_ok=True)
file_ids = set()
# enss = []

# for fn in test_root.glob("*.ann"):
#     file_ids.add(fn.stem)
for fn in test_root.glob("*.txt"):
    txt_fn = fn
    bio_fn = output_root / (fn.stem + ".bio.txt")
    
    txt, sents = pre_processing(txt_fn, deid_pattern=MIMICIII_PATTERN)
    nsents, sent_bound = generate_BIO(sents, [], file_id=fn, no_overlap=False)
    
    BIOdata_to_file(bio_fn, nsents)

2021-01-25 18:33:16,539 INFO sentence boundary detection class initiated.
2021-01-25 18:33:16,540 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:16,540 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/2192394_note_6089.txt ...
2021-01-25 18:33:16,562 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/2192394_note_6089.txt file
2021-01-25 18:33:16,617 INFO sentence boundary detection class initiated.
2021-01-25 18:33:16,618 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:16,619 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/2654416_note_8704.txt ...
2021-01-25 18:33:16,663 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/2654416_note_8704.txt file
2021-01-25 18:33:16,712 INFO sentence boundary detection class initiated.
2021-01-25 18:33:16,713 INFO word level tokenization with replace_numb

2021-01-25 18:33:17,807 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_1742.txt file
2021-01-25 18:33:17,860 INFO sentence boundary detection class initiated.
2021-01-25 18:33:17,861 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:17,862 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_1959.txt ...
2021-01-25 18:33:17,869 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_1959.txt file
2021-01-25 18:33:17,912 INFO sentence boundary detection class initiated.
2021-01-25 18:33:17,913 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:17,914 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_3180.txt ...
2021-01-25 18:33:17,928 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_3180.txt file
2021-01-25 18:33:17,973 INFO sentence boundary detectio

2021-01-25 18:33:18,998 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/1158336_note_2399.txt file
2021-01-25 18:33:19,043 INFO sentence boundary detection class initiated.
2021-01-25 18:33:19,044 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:19,045 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_2248.txt ...
2021-01-25 18:33:19,068 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_2248.txt file
2021-01-25 18:33:19,114 INFO sentence boundary detection class initiated.
2021-01-25 18:33:19,115 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:19,115 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_830.txt ...
2021-01-25 18:33:19,123 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_830.txt file
2021-01-25 18:33:19,168 INFO sentence boundary de

2021-01-25 18:33:20,246 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_1142.txt ...
2021-01-25 18:33:20,271 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_1142.txt file
2021-01-25 18:33:20,319 INFO sentence boundary detection class initiated.
2021-01-25 18:33:20,320 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:20,321 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_3966.txt ...
2021-01-25 18:33:20,337 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_3966.txt file
2021-01-25 18:33:20,383 INFO sentence boundary detection class initiated.
2021-01-25 18:33:20,384 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:20,384 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_7296.txt ...
2021-01-25 18:33:20,392 INFO process /home/ze

2021-01-25 18:33:21,424 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:21,424 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_3232.txt ...
2021-01-25 18:33:21,434 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_3232.txt file
2021-01-25 18:33:21,479 INFO sentence boundary detection class initiated.
2021-01-25 18:33:21,480 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:21,480 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_567.txt ...
2021-01-25 18:33:21,488 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_567.txt file
2021-01-25 18:33:21,533 INFO sentence boundary detection class initiated.
2021-01-25 18:33:21,534 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:21,535 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all

...

2021-01-25 18:33:34,697 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:34,697 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_4009.txt ...
2021-01-25 18:33:34,713 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_4009.txt file
2021-01-25 18:33:34,769 INFO sentence boundary detection class initiated.
2021-01-25 18:33:34,770 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:34,770 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_2444.txt ...
2021-01-25 18:33:34,783 WARNING '7.2 ' cannot be parsed by current rule.
2021-01-25 18:33:34,792 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_2444.txt file
2021-01-25 18:33:34,840 INFO sentence boundary detection class initiated.
2021-01-25 18:33:34,841 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:

2021-01-25 18:33:35,818 WARNING '8.1 per' cannot be parsed by current rule.
2021-01-25 18:33:35,832 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_7927.txt file
2021-01-25 18:33:35,879 INFO sentence boundary detection class initiated.
2021-01-25 18:33:35,879 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:35,880 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_8396.txt ...
2021-01-25 18:33:35,938 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_8396.txt file
2021-01-25 18:33:35,985 INFO sentence boundary detection class initiated.
2021-01-25 18:33:35,985 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:35,986 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/2485605_note_7333.txt ...
2021-01-25 18:33:36,001 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_

2021-01-25 18:33:37,177 INFO sentence boundary detection class initiated.
2021-01-25 18:33:37,178 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:37,179 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_8234.txt ...
2021-01-25 18:33:37,188 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_8234.txt file
2021-01-25 18:33:37,232 INFO sentence boundary detection class initiated.
2021-01-25 18:33:37,233 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:37,234 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_7661.txt ...
2021-01-25 18:33:37,252 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_7661.txt file
2021-01-25 18:33:37,298 INFO sentence boundary detection class initiated.
2021-01-25 18:33:37,299 INFO word level tokenization with replace_number set to False
2021-01-25 18:33

2021-01-25 18:33:38,403 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/2057802_note_5836.txt file
2021-01-25 18:33:38,448 INFO sentence boundary detection class initiated.
2021-01-25 18:33:38,448 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:38,449 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_5884.txt ...
2021-01-25 18:33:38,464 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_5884.txt file
2021-01-25 18:33:38,518 INFO sentence boundary detection class initiated.
2021-01-25 18:33:38,519 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:38,519 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_2442.txt ...
2021-01-25 18:33:38,524 WARNING '7.2 ' cannot be parsed by current rule.
2021-01-25 18:33:38,538 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_not

2021-01-25 18:33:39,674 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/2710850_note_9151.txt ...
2021-01-25 18:33:39,690 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/2710850_note_9151.txt file
2021-01-25 18:33:39,737 INFO sentence boundary detection class initiated.
2021-01-25 18:33:39,738 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:39,739 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_4421.txt ...
2021-01-25 18:33:39,771 INFO process /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_4421.txt file
2021-01-25 18:33:39,819 INFO sentence boundary detection class initiated.
2021-01-25 18:33:39,820 INFO word level tokenization with replace_number set to False
2021-01-25 18:33:39,821 INFO current processing /home/zehao.yu/workspace/py3/dr_ann/data/all_annotated_notes_new/note_209.txt ...
2021-01-25 18:33:39,840 INFO p

In [25]:

#round2
! export CUDA_VISIBLE_DEVICES=1

# use format 1 for BRAT, 2 for BioC, 0 as default for BIO
! MKL_THREADING_LAYER=GNU python ./ClinicalTransformerNER/src/run_transformer_batch_prediction.py \
      --model_type bert \
      --pretrained_model ./new_saved_models/bert \
      --raw_text_dir ./data/all_annotated_notes_new/ \
      --preprocessed_text_dir ./data/bio_new \
      --output_dir ./result/all_notes_result \
      --max_seq_length 128 \
      --do_lower_case \
      --eval_batch_size 8 \
      --log_file ./log2.txt\
      --do_format 1 \
      --do_copy \
      --data_has_offset_information

In [45]:
cat ./log2.txt

2020-12-06 14:36:23 - Transformer_NER - INFO - Task will use cuda device: GPU_0.
2020-12-06 14:36:23 - Transformer_NER - WARNING - set tokenizer as bert-base-uncased
2020-12-06 14:36:23 - Transformer_NER - WARNING - set config as bert-base-uncased
2020-12-06 14:36:23 - Transformer_NER - INFO - Training/evaluation parameters: {'model_type': 'bert', 'pretrained_model': 'bert-base-uncased', 'config_name': 'bert-base-uncased', 'tokenizer_name': 'bert-base-uncased', 'data_dir': './diabetic_retinopathy/bio_les', 'data_has_offset_information': True, 'new_model_dir': './dr_bert_les', 'save_model_core': True, 'predict_output_file': None, 'overwrite_model_dir': True, 'seed': 13, 'max_seq_length': 128, 'do_train': True, 'model_selection_scoring': 'strict-f_score-1', 'do_predict': False, 'use_crf': False, 'do_lower_case': True, 'train_batch_size': 8, 'eval_batch_size': 8, 'train_steps': 1000, 'learning_rate': 1e-05, 'num_train_epochs': 20.0, 'gradient_accumulation_steps': 1, 'do_warmup': True, 'wa

# relation

In [6]:
! git clone https://github.com/uf-hobi-informatics-lab/ClinicalTransformerRelationExtraction.git

Cloning into 'ClinicalTransformerRelationExtraction'...
remote: Enumerating objects: 108, done.
remote: Counting objects: 100% (108/108), done.
remote: Compressing objects: 100% (61/61), done.
remote: Total 108 (delta 58), reused 96 (delta 46), pack-reused 0
Receiving objects: 100% (108/108), 41.57 KiB | 0 bytes/s, done.
Resolving deltas: 100% (58/58), done.


In [5]:
! export CUDA_VISIBLE_DEVICES=0  # indicate no GPU; if you have two GPUs then the IDs for them will be 0 and 1
#MKL_THREADING_LAYER=GNU
! MKL_THREADING_LAYER=GNU python ./ClinicalTransformerNER/src/run_transformer_ner.py \
      --model_type bert \
      --pretrained_model bert-base-uncased \
      --data_dir ./diabetic_retinopathy/bio_les \
      --new_model_dir ./dr_bert_les \
      --overwrite_model_dir \
      --max_seq_length 128 \
      --data_has_offset_information \
      --save_model_core \
      --do_train \

export CUDA_VISIBLE_DEVICES=1
data_dir=./sample_data
nmd=./new_model
pof=./predictions.txt
log=./log.txt

python ./ClinicalTransformerRelationExtraction/src/relation_extraction.py \
		--model_type bert \
		--data_format_mode 0 \
		--classification_scheme 2 \
		--pretrained_model bert-base-uncased \
		--data_dir $data_dir \
		--new_model_dir $nmd \
		--predict_output_file $pof \
		--overwrite_model_dir \
		--seed 13 \
		--max_seq_length 256 \
		--cache_data \
		--do_train \
		--do_predict \
		--do_lower_case \
		--train_batch_size 4 \
		--eval_batch_size 4 \
		--learning_rate 1e-5 \
		--num_train_epochs 3 \
		--gradient_accumulation_steps 1 \
		--do_warmup \
		--warmup_ratio 0.1 \
		--weight_decay 0 \
		--max_num_checkpoints 1 \
		--log_file $log \

str

In [3]:
! python brat_eval.py --f1 ./data/used/test_set --f2 ./result/relation_predicted_results_bert/

******************* Information Extraction Results *******************
                      ------- strict -------    ------ lenient -------
                      Prec.   Rec.    F(b=1)    Prec.   Rec.    F(b=1)
              Lesion  1.0000  1.0000  1.0000    1.0000  1.0000  1.0000
            Eye_part  1.0000  1.0000  1.0000    1.0000  1.0000  1.0000
            Severity  1.0000  1.0000  1.0000    1.0000  1.0000  1.0000
          Laterality  1.0000  1.0000  1.0000    1.0000  1.0000  1.0000
                      ------------------------------------------------
     Overall (micro)  1.0000  1.0000  1.0000    1.0000  1.0000  1.0000
     Overall (macro)  0.9448  0.9448  0.9448    0.9448  0.9448  0.9448

***************************** RELATIONS ******************************
             located  1.0000  0.9286  0.9630    1.0000  0.9286  0.9630
     severity-lesion  0.9454  0.9454  0.9454    0.9454  0.9454  0.9454
   laterality-lesion  0.9139  0.9457  0.9295    0.9139  0.9457  0.9295
     